# How To Improve: An Analysis of Restaurant Orders With The Aim of Improving Customer Experience and Company Performance

The following is an analysis of the order history of two restaurants, with the aim of improving their service level and financial performance. To this end, the following themes will be explored:

- Demand Seasonality
- Product Mix

Following this recommendations will be made based on the observations.

## Data Import

In [0]:
# Creating an object used to load the data
sqlContext

Out[151]: <pyspark.sql.context.SQLContext at 0x7fb87c0d6610>

In [0]:
# Loading order data from both restaurants and assigning it to variables
res_one_orders = sqlContext.read.load('/FileStore/tables/restaurant_1_orders.csv', format='csv', header= True)
res_two_orders = sqlContext.read.load('/FileStore/tables/restaurant_2_orders.csv', format='csv', header= True)


## Data Cleaning

In [0]:
res_one_orders.printSchema()
res_two_orders.printSchema()

root
 |-- Order Number: string (nullable = true)
 |-- Order Date: string (nullable = true)
 |-- Item Name: string (nullable = true)
 |-- Quantity: string (nullable = true)
 |-- Product Price: string (nullable = true)
 |-- Total products: string (nullable = true)

root
 |-- Order ID: string (nullable = true)
 |-- Order Date: string (nullable = true)
 |-- Item Name: string (nullable = true)
 |-- Quantity: string (nullable = true)
 |-- Product Price: string (nullable = true)
 |-- Total products: string (nullable = true)



From the above we see that the two tables contain similar headers.

In [0]:
# Changed res_one_orders header to make them the same
res_one_orders = res_one_orders.withColumnRenamed("Order Number", "Order ID")
# Updating a header to ensure consistency
res_one_orders = res_one_orders.withColumnRenamed("Total products", "Total Products")
res_two_orders = res_two_orders.withColumnRenamed("Total products", "Total Products")

From the above we also see that the two tables contain data in the same formats. However, the data type of every column in both tables is the string data type. We will therefore cast the values of the tables to their appropriate data types.

In [0]:
# Importing functions to be used in upating datatypes
from pyspark.sql.functions import col, rtrim, ltrim

# Trimming white space from the 'Order ID' columns
res_one_orders = res_one_orders.withColumn("Order ID", rtrim(ltrim(col("Order ID"))))
res_two_orders = res_two_orders.withColumn("Order ID", rtrim(ltrim(col("Order ID"))))

# Trimming white space from the 'Item Name' columns
res_one_orders = res_one_orders.withColumn("Item Name", rtrim(ltrim(col("Item Name"))))
res_two_orders = res_two_orders.withColumn("Item Name", rtrim(ltrim(col("Item Name"))))

In [0]:
# Importing function used to convert the data type of the date from string to timestamp
from pyspark.sql.functions import to_timestamp

# Making a column with the date as a timestamp
res_one_orders = res_one_orders.withColumn("Date", to_timestamp(res_one_orders["Order Date"], "dd/MM/yyyy HH:mm"))
res_two_orders = res_two_orders.withColumn("Date", to_timestamp(res_two_orders["Order Date"], "dd/MM/yyyy HH:mm"))

# Replacing the 'Order Date' with the timestamp column named 'Date'
res_one_orders = res_one_orders.withColumn("Order Date", res_one_orders["Date"])
res_one_orders = res_one_orders.drop("Date")
res_two_orders = res_two_orders.withColumn("Order Date", res_two_orders["Date"])
res_two_orders = res_two_orders.drop("Date")

We will now add columns for the day, day of the month, month of the year and year of the products sold

In [0]:
# Adding a 'Day of Week' column
from pyspark.sql.functions import dayofweek
res_one_orders = res_one_orders.withColumn("Day Of Week", dayofweek(col("Order Date")))
res_two_orders = res_two_orders.withColumn("Day Of Week", dayofweek(col("Order Date")))
# Adding a 'Day Of Month' column
from pyspark.sql.functions import dayofmonth
res_one_orders = res_one_orders.withColumn("Day Of Month", dayofmonth(col("Order Date")))
res_two_orders = res_two_orders.withColumn("Day Of Month", dayofmonth(col("Order Date")))
# Adding a 'Month' column
from pyspark.sql.functions import month
res_one_orders = res_one_orders.withColumn("Month", month(col("Order Date")))
res_two_orders = res_two_orders.withColumn("Month", month(col("Order Date")))
# Adding a 'Year' column
from pyspark.sql.functions import year
res_one_orders = res_one_orders.withColumn("Year", year(col("Order Date")))
res_two_orders = res_two_orders.withColumn("Year", year(col("Order Date")))

display(res_one_orders)
display(res_one_orders)

Order ID Order Date Item Name Quantity Product Price Total Products Day Of Week Day Of Month Month Year 16118 2019-08-03T20:25:00.000+0000 Plain Papadum 2 0.8 6 7 3 8 2019 16118 2019-08-03T20:25:00.000+0000 King Prawn Balti 1 12.95 6 7 3 8 2019 16118 2019-08-03T20:25:00.000+0000 Garlic Naan 1 2.95 6 7 3 8 2019 16118 2019-08-03T20:25:00.000+0000 Mushroom Rice 1 3.95 6 7 3 8 2019 16118 2019-08-03T20:25:00.000+0000 Paneer Tikka Masala 1 8.95 6 7 3 8 2019 16118 2019-08-03T20:25:00.000+0000 Mango Chutney 1 0.5 6 7 3 8 2019 16117 2019-08-03T20:17:00.000+0000 Plain Naan 1 2.6 7 7 3 8 2019 16117 2019-08-03T20:17:00.000+0000 Mushroom Rice 1 3.95 7 7 3 8 2019 16117 2019-08-03T20:17:00.000+0000 Tandoori Chicken (1/4) 1 4.95 7 7 3 8 2019 16117 2019-08-03T20:17:00.000+0000 Vindaloo - Lamb 1 7.95 7 7 3 8 2019 16117 2019-08-03T20:17:00.000+0000 Chapati 1 1.95 7 7 3 8 2019 16117 2019-08-03T20:17:00.000+0000 Lamb Tikka 1 4.95 7 7 3 8 2019 16117 2019-08-03T20:17:00.000+0000 Saag Paneer 1 5.95 7 7 3 8 2019 16116 2019-08-03T20:09:00.000+0000 Aloo Chaat 1 4.95 5 7 3 8 2019 16116 2019-08-03T20:09:00.000+0000 Chicken Pakora 1 5.95 5 7 3 8 2019 16116 2019-08-03T20:09:00.000+0000 Chicken Chilli Garlic 1 9.95 5 7 3 8 2019 16116 2019-08-03T20:09:00.000+0000 Lamb Biryani 1 9.95 5 7 3 8 2019 16116 2019-08-03T20:09:00.000+0000 Keema Naan 1 2.95 5 7 3 8 2019 16115 2019-08-03T20:01:00.000+0000 Chicken Pakora 1 5.95 7 7 3 8 2019 16115 2019-08-03T20:01:00.000+0000 Plain Papadum 1 0.8 7 7 3 8 2019 16115 2019-08-03T20:01:00.000+0000 Mango Chutney 1 0.5 7 7 3 8 2019 16115 2019-08-03T20:01:00.000+0000 Red Sauce 1 0.5 7 7 3 8 2019 16115 2019-08-03T20:01:00.000+0000 Korma - Prawn 1 9.95 7 7 3 8 2019 16115 2019-08-03T20:01:00.000+0000 Peshwari Naan 1 2.95 7 7 3 8 2019 16115 2019-08-03T20:01:00.000+0000 Pilau Rice 1 2.95 7 7 3 8 2019 16114 2019-08-03T19:44:00.000+0000 Chicken Balti 1 9.95 2 7 3 8 2019 16114 2019-08-03T19:44:00.000+0000 Special Fried Rice 2 3.95 2 7 3 8 2019 16113 2019-08-03T19:42:00.000+0000 Chicken Tikka Masala 1 8.95 5 7 3 8 2019 16113 2019-08-03T19:42:00.000+0000 Curry - Lamb 1 7.95 5 7 3 8 2019 16113 2019-08-03T19:42:00.000+0000 Pilau Rice 1 2.95 5 7 3 8 2019 16113 2019-08-03T19:42:00.000+0000 Peshwari Naan 1 2.95 5 7 3 8 2019 16113 2019-08-03T19:42:00.000+0000 Plain Papadum 1 0.8 5 7 3 8 2019 16112 2019-08-03T19:41:00.000+0000 Plain Papadum 2 0.8 4 7 3 8 2019 16112 2019-08-03T19:41:00.000+0000 Vegetable Rice 1 3.95 4 7 3 8 2019 16112 2019-08-03T19:41:00.000+0000 Saag - Prawn 1 9.95 4 7 3 8 2019 16112 2019-08-03T19:41:00.000+0000 Tandoori Chicken Masala 1 8.95 4 7 3 8 2019 16111 2019-08-03T19:29:00.000+0000 Pilau Rice 1 2.95 4 7 3 8 2019 16111 2019-08-03T19:29:00.000+0000 Lamb Tikka Chilli Masala 1 8.95 4 7 3 8 2019 16111 2019-08-03T19:29:00.000+0000 Peshwari Naan 1 2.95 4 7 3 8 2019 16111 2019-08-03T19:29:00.000+0000 Saag Aloo 1 5.95 4 7 3 8 2019 16110 2019-08-03T19:28:00.000+0000 Aloo Gobi 1 5.95 8 7 3 8 2019 16110 2019-08-03T19:28:00.000+0000 Bhindi Bhajee 1 5.95 8 7 3 8 2019 16110 2019-08-03T19:28:00.000+0000 Saag Paneer 1 5.95 8 7 3 8 2019 16110 2019-08-03T19:28:00.000+0000 Mint Sauce 2 0.5 8 7 3 8 2019 16110 2019-08-03T19:28:00.000+0000 Chicken Biryani 1 9.95 8 7 3 8 2019 16110 2019-08-03T19:28:00.000+0000 Garlic Naan 1 2.95 8 7 3 8 2019 16110 2019-08-03T19:28:00.000+0000 Plain Naan 1 2.6 8 7 3 8 2019 16110 2019-08-03T19:28:00.000+0000 Tandoori Chicken Masala 1 8.95 8 7 3 8 2019 16109 2019-08-03T19:26:00.000+0000 Plain Papadum 4 0.8 7 7 3 8 2019 16109 2019-08-03T19:26:00.000+0000 Red Sauce 2 0.5 7 7 3 8 2019 16109 2019-08-03T19:26:00.000+0000 Chicken Tikka Masala 1 8.95 7 7 3 8 2019 16109 2019-08-03T19:26:00.000+0000 Madras - Chicken Tikka 1 7.95 7 7 3 8 2019 16109 2019-08-03T19:26:00.000+0000 Mushroom Rice 2 3.95 7 7 3 8 2019 16109 2019-08-03T19:26:00.000+0000 Garlic Naan 1 2.95 7 7 3 8 2019 16109 2019-08-03T19:26:00.000+0000 Bombay Aloo 1 5.95 7 7 3 8 2019 16108 2019-08-03T19:25:00.000+0000 Onion Bhajee 1 3.95 15 7 3 8 2019 16108 2019-08-0

Databricks visualization. Run in Databricks to view.

Order ID Order Date Item Name Quantity Product Price Total Products Day Of Week Day Of Month Month Year 16118 2019-08-03T20:25:00.000+0000 Plain Papadum 2 0.8 6 7 3 8 2019 16118 2019-08-03T20:25:00.000+0000 King Prawn Balti 1 12.95 6 7 3 8 2019 16118 2019-08-03T20:25:00.000+0000 Garlic Naan 1 2.95 6 7 3 8 2019 16118 2019-08-03T20:25:00.000+0000 Mushroom Rice 1 3.95 6 7 3 8 2019 16118 2019-08-03T20:25:00.000+0000 Paneer Tikka Masala 1 8.95 6 7 3 8 2019 16118 2019-08-03T20:25:00.000+0000 Mango Chutney 1 0.5 6 7 3 8 2019 16117 2019-08-03T20:17:00.000+0000 Plain Naan 1 2.6 7 7 3 8 2019 16117 2019-08-03T20:17:00.000+0000 Mushroom Rice 1 3.95 7 7 3 8 2019 16117 2019-08-03T20:17:00.000+0000 Tandoori Chicken (1/4) 1 4.95 7 7 3 8 2019 16117 2019-08-03T20:17:00.000+0000 Vindaloo - Lamb 1 7.95 7 7 3 8 2019 16117 2019-08-03T20:17:00.000+0000 Chapati 1 1.95 7 7 3 8 2019 16117 2019-08-03T20:17:00.000+0000 Lamb Tikka 1 4.95 7 7 3 8 2019 16117 2019-08-03T20:17:00.000+0000 Saag Paneer 1 5.95 7 7 3 8 2019 16116 2019-08-03T20:09:00.000+0000 Aloo Chaat 1 4.95 5 7 3 8 2019 16116 2019-08-03T20:09:00.000+0000 Chicken Pakora 1 5.95 5 7 3 8 2019 16116 2019-08-03T20:09:00.000+0000 Chicken Chilli Garlic 1 9.95 5 7 3 8 2019 16116 2019-08-03T20:09:00.000+0000 Lamb Biryani 1 9.95 5 7 3 8 2019 16116 2019-08-03T20:09:00.000+0000 Keema Naan 1 2.95 5 7 3 8 2019 16115 2019-08-03T20:01:00.000+0000 Chicken Pakora 1 5.95 7 7 3 8 2019 16115 2019-08-03T20:01:00.000+0000 Plain Papadum 1 0.8 7 7 3 8 2019 16115 2019-08-03T20:01:00.000+0000 Mango Chutney 1 0.5 7 7 3 8 2019 16115 2019-08-03T20:01:00.000+0000 Red Sauce 1 0.5 7 7 3 8 2019 16115 2019-08-03T20:01:00.000+0000 Korma - Prawn 1 9.95 7 7 3 8 2019 16115 2019-08-03T20:01:00.000+0000 Peshwari Naan 1 2.95 7 7 3 8 2019 16115 2019-08-03T20:01:00.000+0000 Pilau Rice 1 2.95 7 7 3 8 2019 16114 2019-08-03T19:44:00.000+0000 Chicken Balti 1 9.95 2 7 3 8 2019 16114 2019-08-03T19:44:00.000+0000 Special Fried Rice 2 3.95 2 7 3 8 2019 16113 2019-08-03T19:42:00.000+0000 Chicken Tikka Masala 1 8.95 5 7 3 8 2019 16113 2019-08-03T19:42:00.000+0000 Curry - Lamb 1 7.95 5 7 3 8 2019 16113 2019-08-03T19:42:00.000+0000 Pilau Rice 1 2.95 5 7 3 8 2019 16113 2019-08-03T19:42:00.000+0000 Peshwari Naan 1 2.95 5 7 3 8 2019 16113 2019-08-03T19:42:00.000+0000 Plain Papadum 1 0.8 5 7 3 8 2019 16112 2019-08-03T19:41:00.000+0000 Plain Papadum 2 0.8 4 7 3 8 2019 16112 2019-08-03T19:41:00.000+0000 Vegetable Rice 1 3.95 4 7 3 8 2019 16112 2019-08-03T19:41:00.000+0000 Saag - Prawn 1 9.95 4 7 3 8 2019 16112 2019-08-03T19:41:00.000+0000 Tandoori Chicken Masala 1 8.95 4 7 3 8 2019 16111 2019-08-03T19:29:00.000+0000 Pilau Rice 1 2.95 4 7 3 8 2019 16111 2019-08-03T19:29:00.000+0000 Lamb Tikka Chilli Masala 1 8.95 4 7 3 8 2019 16111 2019-08-03T19:29:00.000+0000 Peshwari Naan 1 2.95 4 7 3 8 2019 16111 2019-08-03T19:29:00.000+0000 Saag Aloo 1 5.95 4 7 3 8 2019 16110 2019-08-03T19:28:00.000+0000 Aloo Gobi 1 5.95 8 7 3 8 2019 16110 2019-08-03T19:28:00.000+0000 Bhindi Bhajee 1 5.95 8 7 3 8 2019 16110 2019-08-03T19:28:00.000+0000 Saag Paneer 1 5.95 8 7 3 8 2019 16110 2019-08-03T19:28:00.000+0000 Mint Sauce 2 0.5 8 7 3 8 2019 16110 2019-08-03T19:28:00.000+0000 Chicken Biryani 1 9.95 8 7 3 8 2019 16110 2019-08-03T19:28:00.000+0000 Garlic Naan 1 2.95 8 7 3 8 2019 16110 2019-08-03T19:28:00.000+0000 Plain Naan 1 2.6 8 7 3 8 2019 16110 2019-08-03T19:28:00.000+0000 Tandoori Chicken Masala 1 8.95 8 7 3 8 2019 16109 2019-08-03T19:26:00.000+0000 Plain Papadum 4 0.8 7 7 3 8 2019 16109 2019-08-03T19:26:00.000+0000 Red Sauce 2 0.5 7 7 3 8 2019 16109 2019-08-03T19:26:00.000+0000 Chicken Tikka Masala 1 8.95 7 7 3 8 2019 16109 2019-08-03T19:26:00.000+0000 Madras - Chicken Tikka 1 7.95 7 7 3 8 2019 16109 2019-08-03T19:26:00.000+0000 Mushroom Rice 2 3.95 7 7 3 8 2019 16109 2019-08-03T19:26:00.000+0000 Garlic Naan 1 2.95 7 7 3 8 2019 16109 2019-08-03T19:26:00.000+0000 Bombay Aloo 1 5.95 7 7 3 8 2019 16108 2019-08-03T19:25:00.000+0000 Onion Bhajee 1 3.95 15 7 3 8 2019 16108 2019-08-0

In [0]:
# Checking that there are no non-whole numbers in the 'Quantity' column
res_one_orders.select(res_one_orders['Quantity'] % 1 != 0).count() == res_one_orders.count()

Out[159]: True

In [0]:
# Checking that there are no non-whole numbers in the 'Quantity' column
res_two_orders.select(res_two_orders["Quantity"] % 1 != 0).count() == res_two_orders.count()

Out[160]: True

In [0]:
# Checking that there are no non-whole numbers in the 'Total Products' column
res_one_orders.select(res_one_orders["Total Products"] % 1 != 0).count() == res_one_orders.count()

Out[161]: True

In [0]:
# Checking that there are no non-whole numbers in the 'Total Products' column
res_two_orders.select(res_two_orders["Total Products"] % 1 != 0).count() == res_two_orders.count()

Out[162]: True

In [0]:
# Casting the 'Quantity' and 'Total Products' column values to integers
res_one_orders = res_one_orders.withColumn("Quantity", res_one_orders['Quantity'].cast('int'))
res_two_orders = res_two_orders.withColumn("Quantity", res_two_orders['Quantity'].cast('int'))
res_one_orders = res_one_orders.withColumn("Total Products", res_one_orders['Total Products'].cast('int'))
res_two_orders = res_two_orders.withColumn("Total Products", res_two_orders['Total Products'].cast('int'))

In [0]:
# Casting the 'Product Price' column values to floats
res_one_orders = res_one_orders.withColumn("Product Price", res_one_orders['Product Price'].cast('float'))
res_two_orders = res_two_orders.withColumn("Product Price", res_two_orders['Product Price'].cast('float'))

In [0]:
# Checking the data types under each column of the two tables
res_one_orders.printSchema()
res_two_orders.printSchema()

root
 |-- Order ID: string (nullable = true)
 |-- Order Date: timestamp (nullable = true)
 |-- Item Name: string (nullable = true)
 |-- Quantity: integer (nullable = true)
 |-- Product Price: float (nullable = true)
 |-- Total Products: integer (nullable = true)
 |-- Day Of Week: integer (nullable = true)
 |-- Day Of Month: integer (nullable = true)
 |-- Month: integer (nullable = true)
 |-- Year: integer (nullable = true)

root
 |-- Order ID: string (nullable = true)
 |-- Order Date: timestamp (nullable = true)
 |-- Item Name: string (nullable = true)
 |-- Quantity: integer (nullable = true)
 |-- Product Price: float (nullable = true)
 |-- Total Products: integer (nullable = true)
 |-- Day Of Week: integer (nullable = true)
 |-- Day Of Month: integer (nullable = true)
 |-- Month: integer (nullable = true)
 |-- Year: integer (nullable = true)



We add total price of the product to the table i.e. product price multiplied by quantity

In [0]:
# Adding a 'Total Price' column
res_one_orders = res_one_orders.withColumn("Total Price", col("Quantity") * col("Product Price"))
res_two_orders = res_two_orders.withColumn("Total Price", col("Quantity") * col("Product Price"))


We will now drop 2015 data, as:
  - There seems to be a gap in the record
  - This may be caused by a temporary closure, and consequently the change may be so significant that it would interfer with
  the analysis as there could be many confounding variables not detailed in the data

In [0]:
# Dropping the 2015 data
res_one_orders = res_one_orders.filter(res_one_orders["Year"] != 2015)
res_two_orders = res_two_orders.filter(res_two_orders["Year"] != 2015)

## Data Analysis

### Seasonality

In [0]:
display(res_one_orders.groupBy("Day Of Week").sum().select("Day Of Week", "sum(Total Price)"))
display(res_two_orders.groupBy("Day Of Week").sum().select("Day Of Week", "sum(Total Price)"))

Day Of Week sum(Total Price) 1 67316.94906365871 6 100563.29859775305 3 38201.29948681593 5 46071.94937765598 4 41248.499440431595 7 112513.64848744869 2 40189.29949456453

Databricks visualization. Run in Databricks to view.

Day Of Week sum(Total Price) 1 101884.498691082 6 146843.94812208414 3 46951.04939365387 5 64109.24917626381 4 52037.799332380295 7 224390.9471321106 2 50848.6993611455

Databricks visualization. Run in Databricks to view.

As the numbers indicating the day of the week start from Sunday, and from the above, we see that there is a clear peak in demand during the week on Friday and Saturday for Restaurant 1, and to a lesser extent on Sunday. For Restaurant 2, it is the same, except that here, it is significantly more busy on Saturdays, compared to Friday.

In [0]:
display(res_one_orders.groupBy("Day Of Month").sum().select("Day Of Month", "sum(Total Price)"))
display(res_two_orders.groupBy("Day Of Month").sum().select("Day Of Month", "sum(Total Price)"))

Day Of Month sum(Total Price) 31 11119.89986306429 28 15380.299786150455 27 14638.399794578552 26 14521.69979262352 12 13298.699803888798 22 14626.899796426296 1 15275.049786806107 13 15324.549800753593 16 15715.54978775978 6 13540.949800908566 3 13914.599806964397 20 12881.999822556973 5 15749.89978390932 19 15522.54980146885 15 14820.949791908264 9 13857.449811697006 17 14945.799782037735 4 13528.09981316328 8 13680.8998183012 23 14875.549787461758 7 13646.09981751442 10 14045.549802184105 25 12504.349828362465 24 14840.649800240993 29 14333.04981470108 21 13545.549822747707 11 13534.249818503857 14 15310.849788725376 2 16736.199765264988 30 13476.749821782112 18 16911.84983587265

Databricks visualization. Run in Databricks to view.

Day Of Month sum(Total Price) 31 16248.999787032604 28 25524.4996663332 27 24863.699681043625 26 21878.99972575903 12 21453.14973706007 22 22237.54971307516 1 25292.04967200756 13 19824.899734556675 16 22653.0997030735 6 21318.24972307682 3 24378.749690294266 20 21443.39973038435 5 20599.449726760387 19 22160.09971421957 15 23412.949702501297 17 23591.84969383478 9 21088.29973000288 4 21988.849725425243 8 21887.249730288982 23 21951.649724185467 7 20437.099734008312 10 22523.2997071743 25 18697.549751222134 24 25373.54967957735 29 23200.59970599413 21 18837.04975914955 11 21521.299728274345 14 22585.399718403816 2 26445.549666702747 30 21741.899726986885 18 21905.149720311165

Databricks visualization. Run in Databricks to view.

From the charts above, it is not clear whether there is a pattern beyond the weekly seasonality of described earlier

In checking for seasonality across a year, we will consider the years 2017 and 2018, as data starts late in 2016 and stops early in 2019

In [0]:
display(res_one_orders.filter(res_one_orders["Year"] != 2016).filter(res_one_orders["Year"] != 2019).groupBy("Month").sum().select("Month", "sum(Total Price)"))
display(res_one_orders.filter(res_one_orders["Year"] != 2016).filter(res_one_orders["Year"] != 2019).groupBy("Month").sum().select("Month", "sum(Total Price)"))

Month sum(Total Price) 12 31450.39957243204 1 21098.749709427357 6 22402.349680006504 3 20533.949721574783 5 20358.44970613718 9 27232.399659335613 4 20281.499730467796 8 22761.399689257145 7 23505.99967753887 10 24616.049655020237 11 25412.049656033516 2 16925.89977288246

Databricks visualization. Run in Databricks to view.

Month sum(Total Price) 12 31450.39957243204 1 21098.749709427357 6 22402.349680006504 3 20533.949721574783 5 20358.44970613718 9 27232.399659335613 4 20281.499730467796 8 22761.399689257145 7 23505.99967753887 10 24616.049655020237 11 25412.049656033516 2 16925.89977288246

Databricks visualization. Run in Databricks to view.

The charts above show both restaurants have a peak during the festive season (i.e. during December), and a smaller peak of demand during October. Therefore, staffing could be increased to meet this demand, and hours of operatio could possibly be extended to satisfy the demand.

### Facility Management

The following section checks seasonality in order size.

In [0]:
display(res_one_orders.groupBy("Order ID").avg().select("Order ID", "avg(Day Of Week)", "avg(Total Products)").groupBy("avg(Day Of Week)").avg())
display(res_two_orders.groupBy("Order ID").avg().select("Order ID", "avg(Day Of Week)", "avg(Total Products)").groupBy("avg(Day Of Week)").avg())

avg(Day Of Week) avg(avg(Day Of Week)) avg(avg(Total Products)) 7.0 7.0 6.0 1.0 1.0 5.375421686746988 4.0 4.0 5.303501945525292 3.0 3.0 5.1819672131147545 2.0 2.0 5.4260504201680675 6.0 6.0 5.867782712675094 5.0 5.0 5.26367461430575

Databricks visualization. Run in Databricks to view.

avg(Day Of Week) avg(avg(Day Of Week)) avg(avg(Total Products)) 7.0 7.0 6.308268281025968 1.0 1.0 6.042244001351808 4.0 4.0 5.567550505050505 3.0 3.0 5.783959537572255 2.0 2.0 5.778217821782178 6.0 6.0 6.237824474660074 5.0 5.0 5.786582144743793

Databricks visualization. Run in Databricks to view.

In [0]:
display(res_one_orders.groupBy("Order ID").avg().select("Order ID", "avg(Day Of Month)", "avg(Total Products)").groupBy("avg(Day Of Month)").avg())
display(res_two_orders.groupBy("Order ID").avg().select("Order ID", "avg(Day Of Month)", "avg(Total Products)").groupBy("avg(Day Of Month)").avg())

avg(Day Of Month) avg(avg(Day Of Month)) avg(avg(Total Products)) 8.0 8.0 5.525821596244131 7.0 7.0 5.462264150943396 29.0 29.0 5.414798206278027 18.0 18.0 5.539149888143177 1.0 1.0 5.670305676855895 25.0 25.0 5.571428571428571 4.0 4.0 5.477832512315271 23.0 23.0 5.718120805369128 31.0 31.0 5.939297124600639 11.0 11.0 5.557739557739557 21.0 21.0 5.61501210653753 14.0 14.0 5.665957446808511 22.0 22.0 5.714285714285714 3.0 3.0 5.545023696682464 19.0 19.0 5.618025751072961 28.0 28.0 5.579175704989154 2.0 2.0 5.650505050505051 17.0 17.0 5.3469827586206895 27.0 27.0 5.615044247787611 10.0 10.0 5.782926829268293 30.0 30.0 5.744949494949495 13.0 13.0 5.6466666666666665 6.0 6.0 5.6725 20.0 20.0 5.445569620253164 5.0 5.0 6.0117096018735365 15.0 15.0 5.685393258426966 24.0 24.0 5.542035398230088 9.0 9.0 5.34331797235023 26.0 26.0 5.873809523809523 16.0 16.0 5.490644490644491 12.0 12.0 5.334123222748815

Databricks visualization. Run in Databricks to view.

avg(Day Of Month) avg(avg(Day Of Month)) avg(avg(Total Products)) 8.0 8.0 5.8003003003003 7.0 7.0 6.248239436619718 29.0 29.0 6.095679012345679 18.0 18.0 6.056872037914692 1.0 1.0 6.048746518105849 25.0 25.0 6.014787430683919 4.0 4.0 6.050314465408805 23.0 23.0 6.237179487179487 31.0 31.0 6.4775413711583925 11.0 11.0 6.045676998368679 21.0 21.0 5.682456140350877 14.0 14.0 5.921481481481481 22.0 22.0 6.316720257234727 3.0 3.0 6.16546762589928 19.0 19.0 6.171749598715891 28.0 28.0 6.226074895977809 2.0 2.0 6.013351134846462 17.0 17.0 6.1422018348623855 27.0 27.0 6.1266187050359715 10.0 10.0 5.881818181818182 30.0 30.0 6.212520593080725 13.0 13.0 5.985964912280702 6.0 6.0 6.055374592833876 20.0 20.0 5.790297339593114 24.0 24.0 6.105263157894737 15.0 15.0 5.960583941605839 5.0 5.0 6.057192374350087 9.0 9.0 6.00805152979066 26.0 26.0 5.947692307692308 16.0 16.0 6.290996784565916 12.0 12.0 6.037337662337662

Databricks visualization. Run in Databricks to view.

In [0]:
display(res_one_orders.filter(res_one_orders["Year"] != 2016).filter(res_one_orders["Year"] != 2019).groupBy("Order ID").avg().select("Order ID", "avg(Month)", "avg(Total Products)").groupBy("avg(Month)").avg())
display(res_two_orders.filter(res_two_orders["Year"] != 2016).filter(res_two_orders["Year"] != 2019).groupBy("Order ID").avg().select("Order ID", "avg(Month)", "avg(Total Products)").groupBy("avg(Month)").avg())

avg(Month) avg(avg(Month)) avg(avg(Total Products)) 8.0 8.0 5.341292134831461 7.0 7.0 5.408469945355192 1.0 1.0 5.833057851239669 4.0 4.0 5.562599049128368 11.0 11.0 5.5955786736020805 3.0 3.0 5.585123966942149 2.0 2.0 5.544921875 10.0 10.0 5.632876712328767 6.0 6.0 5.459940652818991 5.0 5.0 5.545454545454546 9.0 9.0 5.59173126614987 12.0 12.0 5.9425675675675675

Databricks visualization. Run in Databricks to view.

avg(Month) avg(avg(Month)) avg(avg(Total Products)) 8.0 8.0 5.8838427947598255 7.0 7.0 5.895729890764647 1.0 1.0 6.0737786640079765 4.0 4.0 6.180138568129331 11.0 11.0 6.041666666666667 3.0 3.0 6.2593984962406015 2.0 2.0 6.1265432098765435 10.0 10.0 5.882352941176471 6.0 6.0 6.12037037037037 5.0 5.0 6.063976377952756 9.0 9.0 5.9633730834752985 12.0 12.0 6.309914129586261

Databricks visualization. Run in Databricks to view.

There seems to be little variation in the average order size across days of the week, days of the month, and months in the year. This shows a stable order size, which suggests seating can be fixed, as variation would suggest changing seating from large tables to small tables during times where orders contain on average fewer items.

## Summary

To conclude, staffing and inventory should be planned with the view to satisfy the higher demand during the weekends and during the period between October and the New Year. As the order size seems stable over time, seating arrangements can be kept fixed and the facility may not need much adjustment, as the quantity of items varying would hint at larger tables being set up.